# SimRa-Datensatz - Analyse Teil 1

In diesem Notebook führen wir eine explorative Datenanalyse (EDA) für den SimRa-Datensatz durch. Dieser Datensatz enthält alle Angaben zu den aufgezeichneten Beinaheunfällen (`incidents`) in Berlin.
Ziel ist es, ein Verständnis des Datensatzes zu entwickeln und erste Einblicke zu gewinnen.

### Zum SimRa-Datensatz

Im Projekt SimRa werden "Daten darüber, wo es in der Stadt für Radfahrende zu Gefahrenhäufungen kommt, welcher Art diese sind, ob diese zeitlich oder lokal gehäuft auftreten und wo sich die Hauptverkehrsflüsse auf dem Rad bewegen. Hierfür wurde im Projekt eine Smartphone-App entwickelt, die mittels GPS-Daten Fahrtrouten aufzeichnet und dabei Beschleunigungssensoren zum Detektieren von Gefahrensituationen nutzt – bspw. plötzliches Bremsen, Ausweichen oder gar einen Sturz. Im Anschluss an die Fahrt werden Radfahrende gebeten, diese detektierten Gefahrensituationen zu kategorisieren und zu annotieren, etwaige nicht detektierte Gefahrensituationen zu ergänzen und einen Upload auf die Projektserver frei zu geben." (https://www.digital-future.berlin/forschung/projekte/simra/)
    
* Der Datensatz ist öffentlich zugänglich und kann für Projekte genutzt werden. 
* Für unser Projekt nutzen wir den Datensatz zu registrierten Beinahe-Unfällen in Berlin/Potsdam.

## Data Understanding & Data Preparation

Überlegung: Um die Duplikate herauszufiltern, nutzen wir vorerst nahezu den gesamten Datensatz. &rarr; Die letzten beiden Variablen im Datensatz `region` und `i10` beachten wir hierbei nicht, da alle Daten im Datensatz aus der Region Berlin/Potsdam sind und i10 sagt aus, ob ein Electric Scooter beteiligt war oder nicht. Diese Angaben halten wir für die Ermittlung der Duplikate vernachlässigbar. (Da der Aufwand die gesamte csv-Datei korrekt in einen DataFrame einzulesen viel höher wäre als der Nutzen.)

### 1. Laden der Daten

In [10]:
import pandas as pd
import os

# Pfad zur CSV-Datei
file_path = os.path.join("..", "..", "data", "raw_data", "Berlin-incidents.csv")

# Spalten von 0 bis 18 einlesen
df = pd.read_csv(file_path, usecols=range(19))

df.head(3)

lat        lon             ts  bike  childCheckBox  trailerCheckBox  \
0  52.532325  13.394867  1572971392862   1.0              0                0   
1  52.560305  13.354131  1575045211806   3.0              0                0   
2  52.561502  13.354355  1575045239094   3.0              0                0   

   pLoc  incident  i1  i2  i3  i4  i5  i6  i7  i8  i9  scary  \
0   5.0         1   0   0   0   0   0   0   1   0   0      0   
1   0.0         7   0   0   0   0   0   0   1   0   0      0   
2   0.0         7   0   0   0   0   0   0   1   0   0      0   

                                desc  
0                                NaN  
1  haltender PKW auf Fahrradstreifen  
2  haltender PKW auf Fahrradstreifen

### 2. Erste Untersuchung der SimRa-Daten
#### 2.1. Übersicht & grundlegende Statistiken

In [11]:
df.shape

(18038, 19)

In [12]:
df.describe()

lat           lon            ts          bike  childCheckBox  \
count  18038.000000  18038.000000  1.803800e+04  16331.000000   18038.000000   
mean      52.512038     13.378989  1.616061e+12      1.442288       0.011199   
std        0.050011      0.080135  3.703636e+10      1.495991       0.105232   
min       48.147412      8.297819  1.042728e+12      0.000000       0.000000   
25%       52.496301     13.352233  1.583306e+12      1.000000       0.000000   
50%       52.518431     13.380761  1.619546e+12      1.000000       0.000000   
75%       52.536601     13.405134  1.648107e+12      1.000000       0.000000   
max       52.766957     13.885871  1.680767e+12      7.000000       1.000000   

       trailerCheckBox          pLoc      incident            i1  \
count     18038.000000  16331.000000  18038.000000  18038.000000   
mean          0.001552      0.968526      3.338397      0.018960   
std           0.039369      1.493850      2.679353      0.136387   
min           0.000000      0.000000      1.000000      0.000000   
25%           0.000000      0.000000      1.000000      0.000000   
50%           0.000000      0.000000      2.000000      0.000000   
75%           0.000000      2.000000      7.000000      0.000000   
max           1.000000      6.000000      8.000000      1.000000   

                 i2            i3            i4            i5            i6  \
count  18038.000000  18038.000000  18038.000000  18038.000000  18038.000000   
mean       0.058210      0.039749      0.095410      0.038807      0.009203   
std        0.234147      0.195375      0.293788      0.193140      0.095491   
min        0.000000      0.000000      0.000000      0.000000      0.000000   
25%        0.000000      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      0.000000      0.000000      0.000000   
75%        0.000000      0.000000      0.000000      0.000000      0.000000   
max        1.000000      1.000000      1.000000      1.000000      1.000000   

                 i7            i8            i9         scary  
count  18038.000000  18038.000000  18038.000000  18038.000000  
mean       0.596962      0.049174      0.018960      0.291163  
std        0.490522      0.216237      0.136387      0.454311  
min        0.000000      0.000000      0.000000      0.000000  
25%        0.000000      0.000000      0.000000      0.000000  
50%        1.000000      0.000000      0.000000      0.000000  
75%        1.000000      0.000000      0.000000      1.000000  
max        1.000000      1.000000      1.000000      1.000000

### 2.2. Fehlende Werte und Datenqualität

In [13]:
# Anzahl eindeutiger Werte pro Spalte
for col in df.columns:
    print(col)
    print(df[col].nunique())

lat
17762
lon
17774
ts
17803
bike
8
childCheckBox
2
trailerCheckBox
2
pLoc
6
incident
8
i1
2
i2
2
i3
2
i4
2
i5
2
i6
2
i7
2
i8
2
i9
2
scary
2
desc
3880


In [14]:
# Überprüfung auf fehlende Werte
df.isnull().sum()

lat                    0
lon                    0
ts                     0
bike                1707
childCheckBox          0
trailerCheckBox        0
pLoc                1707
incident               0
i1                     0
i2                     0
i3                     0
i4                     0
i5                     0
i6                     0
i7                     0
i8                     0
i9                     0
scary                  0
desc               12359
dtype: int64

In [15]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18038 entries, 0 to 18037
Data columns (total 19 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   lat              18038 non-null  float64
 1   lon              18038 non-null  float64
 2   ts               18038 non-null  int64  
 3   bike             16331 non-null  float64
 4   childCheckBox    18038 non-null  int64  
 5   trailerCheckBox  18038 non-null  int64  
 6   pLoc             16331 non-null  float64
 7   incident         18038 non-null  int64  
 8   i1               18038 non-null  int64  
 9   i2               18038 non-null  int64  
 10  i3               18038 non-null  int64  
 11  i4               18038 non-null  int64  
 12  i5               18038 non-null  int64  
 13  i6               18038 non-null  int64  
 14  i7               18038 non-null  int64  
 15  i8               18038 non-null  int64  
 16  i9               18038 non-null  int64  
 17  scary       

## ProfileReport

In [7]:
from ydata_profiling import ProfileReport
profile = ProfileReport(df, title="Profiling Report")

In [8]:
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

### Umgang mit `Alerts`im DataProfiling

- `highly imbalanced`: Die stark unausgeglichene Daten einzelner Variablen (childBox, trailerCheckBox, i1 bis i9) können vernachlässigt werden &rarr; *Interpretation*: i1-i10 are other participants involved in the incident. 1, if the according type of participant was involved, 0 otherwise.
i1 = Bus/Coach
i2 = Cyclist
i3 = Pedestrian
i4 = Delivery Van
i5 = Lorry/Truck
i6 = Motorcyclist
i7 = Car
i8 = Taxi/Cab
i9 = Other &rarr; Wir gehen davon aus, dass es nachvollziehbar ist, dass die "0" sehr viel häufiger vorkommt als die "1"

- `bike is highly overall correlated with childCheckBox` &rarr; *Interpreation*: childCheckBos = if a child is being transported on the bike, starke Korrelation mit `bike` ist aus unserer Sicht nachvollziehbar und im Rahmen unseres Projekts zu vernachlässigen


- Duplikate: `Dataset has 156 (0.9%) duplicate rows` &rarr; siehe weiter unten

- fehlende Werte `missing values`, `zeros` &rarr; siehe weiter unten

- `lat is highly skewed (γ1 = -37.40688387)` --> siehe Notebook [02_simra_data_analysis](02_simra_data_analysis.ipynb) (Umgang mit Outliern)

## 3. Duplikate

In [16]:
# Duplikate rausfiltern
duplicates = df[df.duplicated(keep=False)]

# Anzahl der Duplikate 
print(f"Anzahl der Duplikate: {len(duplicates)}")

# Duplikate anzeigen
print("Duplikate:")
duplicates.sort_values(by=["lat","lon", "ts"]).head(3)

Anzahl der Duplikate: 377
Duplikate:


lat        lon             ts  bike  childCheckBox  \
6676  52.392973  13.106339  1582007145164   2.0              0   
6677  52.392973  13.106339  1582007145164   2.0              0   
2443  52.396273  13.501354  1563972266320   2.0              0   

      trailerCheckBox  pLoc  incident  i1  i2  i3  i4  i5  i6  i7  i8  i9  \
6676                0   2.0         1   0   0   0   0   0   0   1   0   0   
6677                0   2.0         1   0   0   0   0   0   0   1   0   0   
2443                0   5.0         4   0   0   0   0   0   0   1   0   0   

      scary                                               desc  
6676      1                                                NaN  
6677      1                                                NaN  
2443      0  Entgegenkommender PKW versucht trotz Engstelle...

## Entfernen der Duplikate

In [17]:
# Duplikate entfernen (nur die Duplikate, die in allen Spalten identisch sind)
df_no_duplicates = df.drop_duplicates()

# Überprüfen, ob Duplikate entfernt wurden
print("Anzahl der Zeilen nach Entfernen von Duplikaten:", len(df_no_duplicates))
df_no_duplicates.head(3)

Anzahl der Zeilen nach Entfernen von Duplikaten: 17817


lat        lon             ts  bike  childCheckBox  trailerCheckBox  \
0  52.532325  13.394867  1572971392862   1.0              0                0   
1  52.560305  13.354131  1575045211806   3.0              0                0   
2  52.561502  13.354355  1575045239094   3.0              0                0   

   pLoc  incident  i1  i2  i3  i4  i5  i6  i7  i8  i9  scary  \
0   5.0         1   0   0   0   0   0   0   1   0   0      0   
1   0.0         7   0   0   0   0   0   0   1   0   0      0   
2   0.0         7   0   0   0   0   0   0   1   0   0      0   

                                desc  
0                                NaN  
1  haltender PKW auf Fahrradstreifen  
2  haltender PKW auf Fahrradstreifen

In [18]:
# Speichern der bereinigten Daten ohne Duplikate
# cleaned_data_path = os.path.join("..", "..", "data", "processed_data", "simra_no_duplicates.csv")
# df_no_duplicates.to_csv(cleaned_data_path, index=False)

In [19]:
# Duplikate finden
duplicates = df_no_duplicates[df_no_duplicates.duplicated(keep=False)]

# Anzahl der Duplikate anzeigen
print(f"Anzahl der Duplikate: {len(duplicates)}")
duplicates

Anzahl der Duplikate: 0


Empty DataFrame
Columns: [lat, lon, ts, bike, childCheckBox, trailerCheckBox, pLoc, incident, i1, i2, i3, i4, i5, i6, i7, i8, i9, scary, desc]
Index: []

In [21]:
# Zählen der fehlenden Werte in der Spalte "bike"
missing_bike = df['bike'].isnull().sum()

# Anzeigen der Anzahl der fehlenden Werte
print("Anzahl der fehlenden Werte in der Spalte 'bike':", missing_bike)

# Anzeigen der Zeilen mit fehlenden Werten in der Spalte "bike"
missing_bike_rows = df[df['bike'].isnull()]
print("Zeilen mit fehlenden Werten in der Spalte 'bike':")
print(missing_bike_rows)


Anzahl der fehlenden Werte in der Spalte 'bike': 1707
Zeilen mit fehlenden Werten in der Spalte 'bike':
             lat        lon             ts  bike  childCheckBox  \
8790   52.493841  13.383783  1637225353000   NaN              0   
9082   52.497339  13.328803  1637658536000   NaN              0   
9083   52.490990  13.398203  1637657601000   NaN              0   
9099   52.506252  13.380152  1637744902000   NaN              0   
9706   52.491466  13.376590  1638809897000   NaN              0   
...          ...        ...            ...   ...            ...   
13303  52.505163  13.405646  1631791140000   NaN              0   
13304  52.503373  13.410657  1631791204000   NaN              0   
13305  52.537377  13.374335  1631790013000   NaN              0   
13306  52.524642  13.387653  1631790379000   NaN              0   
14858  52.535517  13.389908  1641158097000   NaN              0   

       trailerCheckBox  pLoc  incident  i1  i2  i3  i4  i5  i6  i7  i8  i9  \
8790         

###  Annahmen und Erklärungen der Nullwerte: 

- **bike** = type of bicycle &rarr; 0 = not chosen &rarr; Fahrt kann auch ohne diese Angabe gespeichert werden, somit können die Nullwerte erklärt werden
- **pLoc** = Location of the phone during the ride &rarr; 0 = Pocket (default value) &rarr; default Wert!! --> Warum so viele Null-Werte? meist auch wenn bike Nullwerte hat &rarr;  **ToDo**: Mail Simra Projekt
- **desc** = text description of the incident &rarr; Fahrt kann auch ohne Angabe einer Beschreibung gespeichert werden. Somit können die Nullwerte erklärt werden.
  

## Nächste Schritte: 
- weitere Vorbereitung der Daten / Data Preparation: siehe Notebook [02_simra_data_analysis](02_simra_data_analysis.ipynb)
    - Outlier identifizieren und entfernen
    - einzene Merkmale extrahieren